# ROR Lookup
### Eric Schares, 1/24/24

The DataCite metadata project needs to identify funders that are US federal funders. We get a list of names (strings) and in some cases a funder ID from the DataCite response.

The funder ID can be ROR, Crossref, ISNI, or none.

Need to take the funder ID and see if the funder is a USFF. Follow each funder all the way up the chain and see if it ends at US Government `https://ror.org/02rcrvv70`

Then could also start at top level US Gov't and go down 1 level, 2 levels, 3 levels to enable matching and comparison across wide spectrum. Would be useful for other projects about USFF...

___

**Crossref** funder IDs come out as full https://doi.org/10.13039/501100000780. But ROR only wants the last part, 501100000780.

See European Commission, https://ror.org/00k4n6c32

**ISNI** IDs come as http://isni.org/isni/0000000449071619. But ROR only wants the last part, AND it has to be broken up into four groups of 4: 0000 0004 4907 1619.

See NASA, https://ror.org/027ka1x80

`https://api.ror.org/organizations?query="501100000780"`

To run a ROR ID itself, use `https://api.ror.org/organizations/010jszw77`

___

### So, two steps here:
1) Convert everything we can to ROR ID - other Notebook
- Crossref and ISNI IDs to ROR
- No ID provided at all to ROR based on name string

2) Once we have a ROR, chase down if it's a USFF. That is, does it end up at the parent US Gov't page?

## Start with 2). Once we have a ROR, chase it all the way up to US Govt

In [1]:
import requests
import pandas as pd
import json

In [2]:
url = 'https://api.ror.org/organizations/010jszw77'  # Delaware Space Grant Consortium. Parent NASA, whose parent is USGovt

In [3]:
api_response = requests.get(url)
api_response

<Response [200]>

In [4]:
parsed_response = api_response.json()
parsed_response

{'id': 'https://ror.org/010jszw77',
 'name': 'Delaware Space Grant Consortium',
 'email_address': None,
 'ip_addresses': [],
 'established': 1991,
 'types': ['Other'],
 'relationships': [{'label': 'National Aeronautics and Space Administration',
   'type': 'Parent',
   'id': 'https://ror.org/027ka1x80'},
  {'label': 'University of Delaware',
   'type': 'Parent',
   'id': 'https://ror.org/01sbq1a82'}],
 'addresses': [{'lat': 39.667394,
   'lng': -75.750253,
   'state': 'Delaware',
   'state_code': 'US-DE',
   'city': 'Newark',
   'geonames_city': {'id': 4143861,
    'city': 'Newark',
    'geonames_admin1': {'name': 'Delaware',
     'id': 4142224,
     'ascii_name': 'Delaware',
     'code': 'US.DE'},
    'geonames_admin2': {'name': 'New Castle County',
     'id': 4143835,
     'ascii_name': 'New Castle County',
     'code': 'US.DE.003'},
    'license': {'attribution': 'Data from geonames.org under a CC-BY 3.0 license',
     'license': 'http://creativecommons.org/licenses/by/3.0/'},
    '

In [7]:
#for result in parsed_response['data']:    # don't need to loop since you'll only find one. You gave it a specific ROR ID.
ror_id = parsed_response['id']
name = parsed_response['name']

In [8]:
print(ror_id, name)

https://ror.org/010jszw77 Delaware Space Grant Consortium


In [10]:
num_relationships = len(parsed_response['relationships'])
print(f"Found {num_relationships} relationships")

for i in range(0, num_relationships):
    if(parsed_response['relationships'][i]['type']) == "Parent":
        print("parent")
        if parsed_response['relationships'][i]['label'] == "Government of the United States of America":
            USFF = True
        else:
            1
            #kick off recursive run up the chain
    else:
        1 #not a parent, do nothing
            

Found 2 relationships
parent
parent


##  Match funders to ROR IDs and see if it's a US federal funder
Could follow each funder all the way up the chain and see if it ends at US Government `https://ror.org/02rcrvv70`

Then could also start at top level US Gov't and go down 1 level, 2 levels, 3 levels to enable matching and comparison across wide spectrum. Would be useful for other projects about USFF...

In [11]:
# Stack Overflow user Grismar
def has_US_govt_parent(org_id: str, visited: dict[str, bool] = None) -> bool:
    """
    Returns True if the organization with the given ROR ID has a parent organization
    that is the Government of the United States of America, False otherwise.
    """
    print(f'Checking {org_id}')
    
    # start with an empty cache
    if visited is None:
        visited = {}

    # if you passed me None, just give it back
    if (org_id == 'None') or (org_id is None):
        return None
    if (org_id in ['nan', 'NaN', 'float', 'No results', 'numeric', 'Multiple results']):
        return None
#     if isinstance(org_id, float):  #.isnumeric():
#         return "float"
    
    # check it here, if we've done it already we're done
    if org_id in visited:
        print(f'Already found {org_id}')
        return visited[org_id]

    # - load the data for an organisation
    #print(f'Loading data for {org_id}')
    
    url = f'https://api.ror.org/organizations/{org_id}'
    api_response = requests.get(url)
    parsed_response = api_response.json()

    # assume we won't find the US govt.
    result = False

    # - for each of its relationships
    # you don't need the number of relationships and index it, you can just loop over the members
    for relationship in parsed_response['relationships']:
        # - check if it is a parent
        if relationship['type'] == "Parent":
            # -if so, check if it is the US government
            if relationship['label'] == "Government of the United States of America":
            #if relationship['label'] == "University of Delaware":
                result = True
                break
            else:
                # assuming that the last part without slashes is the actual ID, there's many ways to do this
                parent_id = relationship['id'].split('/')[-1]
                # - call the recursive function
                #print(f'Need to check parents of {relationship["label"]}, {parent_id}')
                if has_US_govt_parent(parent_id, visited):
                    result = True
                    break
        else:
            pass # not a parent

    # remember we already visited this org id, record its status
    print(f"RESULT {result}")
    visited[org_id] = result

    # - if we didn't return True already, none were the US govt. or had it as a (grand)parent, return False
    return result

In [14]:
# read in things you already tested
USFF_visited = json.load(open('Is_ROR_a_USFF_visited_dict.txt',))

In [15]:
# Testing

#USFF_visited = {}
orgs = ['00fe3cc74', '010jszw77', '00k4n6c32']
# Iowa Space Grant Consortium, should be true through NASA (2nd parent)
# Delaware Space Grant Consortium, should be true through NASA (1st parent)
# European Commission, should be false

for org in orgs:
    print(f'\nChecking {org}')
   
    if has_US_govt_parent(org, USFF_visited):
        print(f'{org} has a US government parent')
    else:
        print(f'{org} does not have a US government parent')

print('\nVisited: ', USFF_visited)


Checking 00fe3cc74
Checking 00fe3cc74
Already found 00fe3cc74
00fe3cc74 has a US government parent

Checking 010jszw77
Checking 010jszw77
Already found 010jszw77
010jszw77 has a US government parent

Checking 00k4n6c32
Checking 00k4n6c32
Already found 00k4n6c32
00k4n6c32 does not have a US government parent

Visited:  {'04rswrd78': False, '027ka1x80': True, '00fe3cc74': True, '010jszw77': True, '019w4f821': False, '00k4n6c32': False, '01bj3aw27': True, '021nxhr62': True, '001aqnf71': False, 'https://ror.org/0439y7842': False, '0314h5y94': False, '02wa0fq92': False, 'https://ror.org/05mmh0f86': False, '001xhss06': True, '03g87he71': True, '014bj5w56': True, '00whkrf32': True, 'https://ror.org/025g6sc95': True, 'https://ror.org/021nxhr62': True, 'https://ror.org/04pz7b180': False, 'https://ror.org/03wnrjx87': False, 'https://ror.org/012mzw131': False, 'https://ror.org/059bp8k51': False, 'https://ror.org/03x94j517': False, 'https://ror.org/054225q67': False, 'https://ror.org/0472cxd90': 

In [16]:
type(USFF_visited)

dict

In [17]:
print(USFF_visited_2)

NameError: name 'USFF_visited_2' is not defined

In [3]:
# read it back in
USFF_visited = json.load(open('Is_ROR_a_USFF_visited_dict.txt',))

In [18]:
len(USFF_visited)

6731

# Scale up to run on a whole df

In [2]:
df = pd.read_csv('2023.csv')

C:\Users\eschares\AppData\Local\Temp\ipykernel_22280\1203902614.py:1: DtypeWarning: Columns (5,6,12,17,18) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('2023.csv')


In [3]:
df.head(3)

top_id  publicationyear  \
0  10.18465/mnt_la_faute_sur_mer_2013             2023   
1  10.18465/mnt_la_faute_sur_mer_2013             2023   
2      10.18465/mnt_jard_sur_mer_2013             2023   

                                  doi  \
0  10.18465/mnt_la_faute_sur_mer_2013   
1  10.18465/mnt_la_faute_sur_mer_2013   
2      10.18465/mnt_jard_sur_mer_2013   

                                           publisher  \
0  Observatoire des Sciences de l'Univers Nantes ...   
1  Observatoire des Sciences de l'Univers Nantes ...   
2  Observatoire des Sciences de l'Univers Nantes ...   

                                            subjects relatedIdentifiers sizes  \
0  [{'subject': 'Géomorphologie', 'valueUri': ''}...                NaN   NaN   
1  [{'subject': 'Géomorphologie', 'valueUri': ''}...                NaN   NaN   
2  [{'subject': 'Géomorphologie', 'valueUri': ''}...                NaN   NaN   

  formats rightsIdentifier                                           creators  \
0     NaN              NaN  [{'name': 'Launeau, Patrick', 'nameType': 'Per...   
1     NaN              NaN  [{'name': 'Launeau, Patrick', 'nameType': 'Per...   
2     NaN              NaN  [{'name': 'Launeau, Patrick', 'nameType': 'Per...   

   num_funders awardTitle awardNumber  \
0            2        NaN         NaN   
1            2        NaN         NaN   
2            2        NaN         NaN   

                                         funder_name  \
0  Direction Régionale de l'Environnement, de l'A...   
1              Conseil Régional des Pays de la Loire   
2  Direction Régionale de l'Environnement, de l'A...   

                        funderidentifier funderidentifiertype     ROR_ID  \
0                                    NaN                  NaN       None   
1  https://doi.org/10.13039/501100013414   Crossref Funder ID  01zsm1k25   
2                                    NaN                  NaN       None   

    USFF USFF_2  
0   None   None  
1  False  False  
2   None   None

In [4]:
df.shape

(365314, 19)

### Save the `USFF_visited` dictionary

In [98]:
# save to file
json.dump(USFF_visited, open('USFF_visited_dict.txt', 'w'))

In [53]:
USFF_visited = json.load(open('USFF_visited_dict.txt',))

In [97]:
len(USFF_visited)

6739

## Run it

In [157]:
USFF_visited_2 = dict()

In [158]:
USFF_visited_2

{}

In [159]:
%%time
df['USFF_2'] = df['ROR_ID'].apply(has_US_govt_parent, visited=USFF_visited_2)
# 7m 27s, 9m 16s

Checking None
Checking 01zsm1k25
RESULT False
Checking None
Checking 01zsm1k25
Already found 01zsm1k25
Checking None
Checking 01zsm1k25
Already found 01zsm1k25
Checking None
Checking 01zsm1k25
Already found 01zsm1k25
Checking None
Checking 01zsm1k25
Already found 01zsm1k25
Checking None
Checking 01zsm1k25
Already found 01zsm1k25
Checking None
Checking 01zsm1k25
Already found 01zsm1k25
Checking None
Checking 01zsm1k25
Already found 01zsm1k25
Checking 0029jxk29
RESULT False
Checking 021nxhr62
RESULT True
Checking 021nxhr62
Already found 021nxhr62
Checking 021nxhr62
Already found 021nxhr62
Checking 021nxhr62
Already found 021nxhr62
Checking 0029jxk29
Already found 0029jxk29
Checking 00k4n6c32
Checking 019w4f821
RESULT False
RESULT False
Checking 00k4n6c32
Already found 00k4n6c32
Checking 00k4n6c32
Already found 00k4n6c32
Checking https://ror.org/03zttf063
RESULT False
Checking 02bxrrf91
RESULT False
Checking https://ror.org/054225q67
RESULT False
Checking https://ror.org/03zttf063
Already

RESULT False
Checking 0439y7842
Already found 0439y7842
Checking 00rbzpz17
RESULT False
Checking None
Checking None
Checking https://ror.org/04jsz6e67
RESULT False
Checking 01h531d29
RESULT False
Checking 0439y7842
Already found 0439y7842
Checking 00yjd3n13
Already found 00yjd3n13
Checking 00yjd3n13
Already found 00yjd3n13
Checking 003x0zc53
Checking 05r0vyz12
RESULT False
RESULT False
Checking 003x0zc53
Already found 003x0zc53
Checking 00snfqn58
Already found 00snfqn58
Checking 00snfqn58
Already found 00snfqn58
Checking None
Checking 003x0zc53
Already found 003x0zc53
Checking 003x0zc53
Already found 003x0zc53
Checking 003x0zc53
Already found 003x0zc53
Checking 003x0zc53
Already found 003x0zc53
Checking 003x0zc53
Already found 003x0zc53
Checking 02d290r06
RESULT False
Checking https://ror.org/027ka1x80
RESULT True
Checking https://ror.org/027ka1x80
Already found https://ror.org/027ka1x80
Checking 00k4n6c32
Already found 00k4n6c32
Checking 00k4n6c32
Already found 00k4n6c32
Checking 00k4

Checking 001aqnf71
Already found 001aqnf71
RESULT False
Checking 029chgv08
Already found 029chgv08
Checking 05j159997
RESULT False
Checking 0566bfb96
Already found 0566bfb96
Checking None
Checking None
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 04jsz6e67
Already found 04jsz6e67
Checking 0566bfb96
Already found 0566bfb96
Checking 0566bfb96
Already found 0566bfb96
Checking 00k4n6c32
Already found 00k4n6c32
Checking 027ka1x80
Already found 027ka1x80
Checking 04jsz6e67
Already found 04jsz6e67
Checking 01deh9c76
RESULT False
Checking 0566bfb96
Already found 0566bfb96
Checking 0439y7842
Already found 0439y7842
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 00k4n6c32
Already found 00k4n6c32
Checking 027ka1x80
Already found 02

RESULT False
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 00apvva27
Checking 021nxhr62
Already found 021nxhr62
RESULT True
Checking 001xhss06
Already found 001xhss06
Checking 001xhss06
Already found 001xhss06
Checking 001xhss06
Already found 001xhss06
Checking 05p847d66
Already found 05p847d66
Checking 00k4n6c32
Already found 00k4n6c32
Checking 027ka1x80
Already found 027ka1x80
Checking N

Checking 021nxhr62
Already found 021nxhr62
RESULT True
Checking 0439y7842
Already found 0439y7842
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 00k4n6c32
Already found 00k4n6c32
Checking 0439y7842
Already found 0439y7842
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking https://ror.org/027ka1x80
Already found https://ror.org/027ka1x80
Checking 027ka1x80
Already found 027ka1x80
Checking 0

...

RESULT False
Checking 037n8p820
Already found 037n8p820
Checking 037n8p820
Already found 037n8p820
Checking 037n8p820
Already found 037n8p820
Checking None
Checking None
Checking None
Checking None
Checking https://ror.org/021nxhr62
Already found https://ror.org/021nxhr62
Checking https://ror.org/02yh9se80
Already found https://ror.org/02yh9se80
Checking https://ror.org/021nxhr62
Already found https://ror.org/021nxhr62
Checking https://ror.org/02yh9se80
Already found https://ror.org/02yh9se80
Checking 055546q82
Already found 055546q82
Checking 055546q82
Already found 055546q82
Checking 037n8p820
Already found 037n8p820
Checking 03613d656
Already found 03613d656
Checking 037n8p820
Already found 037n8p820
Checking 03613d656
Already found 03613d656
Checking 00j8z2m73
Already found 00j8z2m73
Checking 00tntzp09
Already found 00tntzp09
Checking 04sazxf24
Already found 04sazxf24
Checking 04sazxf24
Already found 04sazxf24
Checking 0597re059
RESULT False
Checking 01n6e6j62
Already found 01n6e6j

RESULT False
Checking 00yjd3n13
Already found 00yjd3n13
Checking 00yjd3n13
Already found 00yjd3n13
Checking 021nxhr62
Already found 021nxhr62
Checking 021nxhr62
Already found 021nxhr62
Checking 00j8z2m73
Already found 00j8z2m73
Checking 00j8z2m73
Already found 00j8z2m73
Checking 00k4n6c32
Already found 00k4n6c32
Checking 00k4n6c32
Already found 00k4n6c32
Checking 021nxhr62
Already found 021nxhr62
Checking 021nxhr62
Already found 021nxhr62
Checking 04jsz6e67
Already found 04jsz6e67
Checking 021nxhr62
Already found 021nxhr62
Checking 05bnh6r87
Already found 05bnh6r87
Checking 012a77v79
RESULT False
Checking 049zxm836
RESULT False
Checking 00rs6vg23
Already found 00rs6vg23
Checking 00rs6vg23
Already found 00rs6vg23
Checking 00hhkn466
Already found 00hhkn466
Checking None
Checking 01nmpj461
Already found 01nmpj461
Checking 00hhkn466
Already found 00hhkn466
Checking 00hhkn466
Already found 00hhkn466
Checking 00hhkn466
Already found 00hhkn466
Checking 00hhkn466
Already found 00hhkn466
Checki

RESULT False
Checking 01h531d29
Already found 01h531d29
Checking 015pzp858
Already found 015pzp858
Checking 021nxhr62
Already found 021nxhr62
Checking 02g98ya79
Already found 02g98ya79
Checking 03f20jx79
Already found 03f20jx79
Checking 0314h5y94
Already found 0314h5y94
Checking 05mmh0f86
Already found 05mmh0f86
Checking 05mmh0f86
Already found 05mmh0f86
Checking 047272k79
Already found 047272k79
Checking 04q48ey07
Already found 04q48ey07
Checking 04q48ey07
Already found 04q48ey07
Checking 04q48ey07
Already found 04q48ey07
Checking 01cwqze88
Already found 01cwqze88
Checking 03x94j517
Already found 03x94j517
Checking 02b5d8509
Already found 02b5d8509
Checking 01cwqze88
Already found 01cwqze88
Checking 049v75w11
Already found 049v75w11
Checking 049v75w11
Already found 049v75w11
Checking 049v75w11
Already found 049v75w11
Checking 049v75w11
Already found 049v75w11
Checking 00k4n6c32
Already found 00k4n6c32
Checking None
Checking 00hhkn466
Already found 00hhkn466
Checking 00hhkn466
Already 

RESULT False
Checking 01h0zpd94
Already found 01h0zpd94
Checking 034t30j35
Already found 034t30j35
Checking 02rz58g17
Checking 034t30j35
Already found 034t30j35
RESULT False
Checking 02kgve346
Already found 02kgve346
Checking https://ror.org/035a68863
Checking 03v0pmy70
Already found 03v0pmy70
RESULT True
Checking 021nxhr62
Already found 021nxhr62
Checking No results
Checking 021nxhr62
Already found 021nxhr62
Checking None
Checking 052csg198
Already found 052csg198
Checking 033jmdj81
Checking 02xznz413
Already found 02xznz413
RESULT True
Checking None
Checking None
Checking 012mzw131
Already found 012mzw131
Checking 00k4n6c32
Already found 00k4n6c32
Checking None
Checking None
Checking None
Checking None
Checking None
Checking 0271asj38
Already found 0271asj38
Checking 03bea9k73
Already found 03bea9k73
Checking 01c4rxk68
Checking 04a1a1e81
RESULT False
Checking 03bea9k73
Already found 03bea9k73
Checking 01hxy9878
Already found 01hxy9878
Checking 02tyrky19
RESULT False
Checking 03265fv1

RESULT False
Checking 0439y7842
Already found 0439y7842
Checking 01s5ya894
Already found 01s5ya894
Checking 033hnyq61
Already found 033hnyq61
Checking None
Checking 021nxhr62
Already found 021nxhr62
Checking None
Checking 023jta124
Already found 023jta124
Checking 00epmv149
Already found 00epmv149
Checking 00epmv149
Already found 00epmv149
Checking 04aha0598
Already found 04aha0598
Checking 01tmp8f25
Already found 01tmp8f25
Checking 00yjd3n13
Already found 00yjd3n13
Checking 00yjd3n13
Already found 00yjd3n13
Checking 00yjd3n13
Already found 00yjd3n13
Checking 00yjd3n13
Already found 00yjd3n13
Checking 03r8z3t63
Already found 03r8z3t63
Checking 03r8z3t63
Already found 03r8z3t63
Checking 00cjrc276
Already found 00cjrc276
Checking 03cx3d993
Already found 03cx3d993
Checking No results
Checking None
Checking 01h531d29
Already found 01h531d29
Checking 001w7jn25
Already found 001w7jn25
Checking 00vt3ry76
RESULT False
Checking 04pz7b180
Already found 04pz7b180
Checking 00f54p054
Already found 

In [56]:
df[df['ROR_ID']=='float']

top_id  publicationyear                doi  \
2962    10.3886/e183867             2023    10.3886/e183867   
2963  10.3886/e183867v1             2023  10.3886/e183867v1   

                                              publisher subjects  \
2962  ICPSR - Interuniversity Consortium for Politic...      NaN   
2963  ICPSR - Interuniversity Consortium for Politic...      NaN   

                                     relatedIdentifiers sizes formats  \
2962  [{'relationType': 'HasVersion', 'relatedIdenti...   NaN     NaN   
2963  [{'relationType': 'IsVersionOf', 'relatedIdent...   NaN     NaN   

     rightsIdentifier                                           creators  \
2962              NaN  [{'name': 'Guthery, Sarah', 'nameType': 'Perso...   
2963              NaN  [{'name': 'Guthery, Sarah', 'nameType': 'Perso...   

      num_funders awardTitle awardNumber funder_name funderidentifier  \
2962            1        NaN     <empty>         NaN              NaN   
2963            1        NaN     <empty>         NaN              NaN   

     funderidentifiertype ROR_ID  
2962                  NaN  float  
2963                  NaN  float

In [ ]:
df.iloc[2962]['funder_name']  # it's a float called nan, usually things are a str
#df.iloc[2960:2970]

In [110]:
# save to file
json.dump(USFF_visited_2, open('Is_ROR_a_USFF_visited_dict_2.txt', 'w'))

In [111]:
len(USFF_visited_2)

3513

In [5]:
df.head(4)

top_id  publicationyear  \
0  10.18465/mnt_la_faute_sur_mer_2013             2023   
1  10.18465/mnt_la_faute_sur_mer_2013             2023   
2      10.18465/mnt_jard_sur_mer_2013             2023   
3      10.18465/mnt_jard_sur_mer_2013             2023   

                                  doi  \
0  10.18465/mnt_la_faute_sur_mer_2013   
1  10.18465/mnt_la_faute_sur_mer_2013   
2      10.18465/mnt_jard_sur_mer_2013   
3      10.18465/mnt_jard_sur_mer_2013   

                                           publisher  \
0  Observatoire des Sciences de l'Univers Nantes ...   
1  Observatoire des Sciences de l'Univers Nantes ...   
2  Observatoire des Sciences de l'Univers Nantes ...   
3  Observatoire des Sciences de l'Univers Nantes ...   

                                            subjects relatedIdentifiers sizes  \
0  [{'subject': 'Géomorphologie', 'valueUri': ''}...                NaN   NaN   
1  [{'subject': 'Géomorphologie', 'valueUri': ''}...                NaN   NaN   
2  [{'subject': 'Géomorphologie', 'valueUri': ''}...                NaN   NaN   
3  [{'subject': 'Géomorphologie', 'valueUri': ''}...                NaN   NaN   

  formats rightsIdentifier                                           creators  \
0     NaN              NaN  [{'name': 'Launeau, Patrick', 'nameType': 'Per...   
1     NaN              NaN  [{'name': 'Launeau, Patrick', 'nameType': 'Per...   
2     NaN              NaN  [{'name': 'Launeau, Patrick', 'nameType': 'Per...   
3     NaN              NaN  [{'name': 'Launeau, Patrick', 'nameType': 'Per...   

   num_funders awardTitle awardNumber  \
0            2        NaN         NaN   
1            2        NaN         NaN   
2            2        NaN         NaN   
3            2        NaN         NaN   

                                         funder_name  \
0  Direction Régionale de l'Environnement, de l'A...   
1              Conseil Régional des Pays de la Loire   
2  Direction Régionale de l'Environnement, de l'A...   
3              Conseil Régional des Pays de la Loire   

                        funderidentifier funderidentifiertype     ROR_ID  \
0                                    NaN                  NaN       None   
1  https://doi.org/10.13039/501100013414   Crossref Funder ID  01zsm1k25   
2                                    NaN                  NaN       None   
3  https://doi.org/10.13039/501100013414   Crossref Funder ID  01zsm1k25   

    USFF USFF_2  
0   None   None  
1  False  False  
2   None   None  
3  False  False

In [115]:
df.to_csv('2023.csv', index=False)

## Now we have each row classified by USFF T/F

In [9]:
df['USFF'].value_counts()

False    196600
False    148014
True      15430
None       5260
True          8
Name: USFF, dtype: int64

In [11]:
df['USFF_2'].value_counts()

False    196600
False    146356
True      15429
None       5260
True          8
Name: USFF_2, dtype: int64

In [91]:
#USFF_df = pd.read_csv('2020_USFF.csv')
USFF_df.shape

(15438, 19)

In [12]:
#USFF_df['USFF'].value_counts()
df['USFF_2'].value_counts()

False    196600
False    146356
True      15429
None       5260
True          8
Name: USFF_2, dtype: int64

In [162]:
#t_f_counts = df['USFF_2'].value_counts().reset_index()#.rename(columns={"index": "T/F", 'funder_name': "count"})
#t_f_counts

index  USFF_2
0  False  342956
1   True   15437

In [154]:
#t_f_counts['index'][0]

False

In [155]:
#t_f_counts['index'][1]

'False'

In [5]:
USFF_df.head(3)

top_id  publicationyear                  doi publisher  \
0  10.5061/dryad.j8227             2019  10.5061/dryad.j8227     Dryad   
1  10.5061/dryad.j8227             2019  10.5061/dryad.j8227     Dryad   
2  10.5061/dryad.j8227             2019  10.5061/dryad.j8227     Dryad   

                                            subjects  \
0  [{'subject': 'Populus nigra × P. maximowiczii'...   
1  [{'subject': 'Populus nigra × P. maximowiczii'...   
2  [{'subject': 'Populus nigra × P. maximowiczii'...   

                                  relatedIdentifiers          sizes formats  \
0  [{'relationType': 'IsCitedBy', 'relatedIdentif...  1624479 bytes     NaN   
1  [{'relationType': 'IsCitedBy', 'relatedIdentif...  1624479 bytes     NaN   
2  [{'relationType': 'IsCitedBy', 'relatedIdentif...  1624479 bytes     NaN   

  rightsIdentifier                                           creators  \
0          cc0-1.0  [{'name': 'Oates, Lawrence G.', 'nameType': 'P...   
1          cc0-1.0  [{'name': 'Oates, Lawrence G.', 'nameType': 'P...   
2          cc0-1.0  [{'name': 'Oates, Lawrence G.', 'nameType': 'P...   

   num_funders awardTitle        awardNumber  \
0            3        NaN  DE‐FC02‐07ER64494   
1            3        NaN  DE-ACO5-76RL01830   
2            3        NaN        DEB 1637653   

                          funder_name           funderidentifier  \
0  United States Department of Energy  https://ror.org/01bj3aw27   
1  United States Department of Energy  https://ror.org/01bj3aw27   
2         National Science Foundation  https://ror.org/021nxhr62   

  funderidentifiertype     ROR_ID  USFF ROR_cleaned  
0                  ROR  01bj3aw27  True   01bj3aw27  
1                  ROR  01bj3aw27  True   01bj3aw27  
2                  ROR  021nxhr62  True   021nxhr62

In [163]:
# select USFF true, collapse by DOI, get a final count
USFF_df = df[ df['USFF_2']==True ]
USFF_df.sample(5)

top_id  publicationyear                      doi  \
356962  10.5061/dryad.x0k6djhrd             2023  10.5061/dryad.x0k6djhrd   
12161          10.18128/d120.v2             2023         10.18128/d120.v2   
941              10.25574/25127             2023           10.25574/25127   
3208             10.25574/26844             2023           10.25574/26844   
354670  10.5281/zenodo.10161336             2023  10.5281/zenodo.10161336   

                       publisher  \
356962                     Dryad   
12161     Minneapolis, MN: IPUMS   
941     Chandra X-ray Center/SAO   
3208    Chandra X-ray Center/SAO   
354670                    Zenodo   

                                                 subjects  \
356962  [{'subject': 'FOS: Biological sciences', 'subj...   
12161                                                 NaN   
941     [{'subject': 'High Energy Astrophysics Data/X-...   
3208    [{'subject': 'High Energy Astrophysics Data/X-...   
354670                                                NaN   

                                       relatedIdentifiers  \
356962  [{'relationType': 'IsCitedBy', 'relatedIdentif...   
12161   [{'relationType': 'IsNewVersionOf', 'relatedId...   
941                                                   NaN   
3208                                                  NaN   
354670  [{'relationType': 'IsVersionOf', 'relatedIdent...   

                        sizes   formats rightsIdentifier  \
356962      68233863190 bytes       NaN          cc0-1.0   
12161                     NaN       NaN              NaN   
941        ks 28.613559419108  ['FITS']              NaN   
3208    ks 5.9782556557028999  ['FITS']              NaN   
354670                    NaN       NaN              NaN   

                                                 creators  num_funders  \
356962  [{'name': 'Kim, Bernard', 'nameType': 'Persona...            2   
12161   [{'name': 'Kugler, Tracy A.', 'givenName': 'Tr...            2   
941     [{'name': 'CXC-DS', 'nameType': 'Organizationa...            1   
3208    [{'name': 'CXC-DS', 'nameType': 'Organizationa...            1   
354670  [{'name': 'Weiss, David A', 'nameType': 'Perso...            8   

                                               awardTitle      awardNumber  \
356962                                                NaN      F32GM135998   
12161                                                 NaN     R01 ES034788   
941                                  Chandra X-ray Center      NAS-8-03060   
3208                                 Chandra X-ray Center      NAS-8-03060   
354670  Crossing space and time: uncovering the nonlin...  1R01EB029857-01   

                                           funder_name  \
356962  National Institute of General Medical Sciences   
12161                    National Institutes of Health   
941                                               NASA   
3208                                              NASA   
354670                   National Institutes of Health   

                             funderidentifier funderidentifiertype  \
356962              https://ror.org/04q48ey07                  ROR   
12161                                     NaN                  NaN   
941     http://isni.org/isni/0000000449071619                 ISNI   
3208                         0000000449071619                 ISNI   
354670                              01cwqze88                  ROR   

                           ROR_ID  USFF USFF_2  
356962                  04q48ey07  True   True  
12161   https://ror.org/01cwqze88  True   True  
941                     027ka1x80  True   True  
3208                    027ka1x80  True   True  
354670                  01cwqze88  True   True

In [166]:
USFF_df.shape

(15437, 20)

In [164]:
# Standardize the ROR column, some are just the ID, some are a link.
# If you want to count them, you need to have them in the same format
USFF_df['ROR_cleaned'] = [x.split('/')[-1] for x in USFF_df['ROR_ID']]

C:\Users\eschares\AppData\Local\Temp\ipykernel_13240\1848340483.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  USFF_df['ROR_cleaned'] = [x.split('/')[-1] for x in USFF_df['ROR_ID']]


In [165]:
USFF_df.sample(5)

top_id  publicationyear  \
30687                    10.25574/27861             2023   
1675                     10.25574/26045             2023   
346487  10.6084/m9.figshare.19303928.v1             2023   
354592                   10.5524/102485             2023   
20065           10.5061/dryad.7sqv9s4x3             2023   

                                    doi                 publisher  \
30687                    10.25574/27861  Chandra X-ray Center/SAO   
1675                     10.25574/26045  Chandra X-ray Center/SAO   
346487  10.6084/m9.figshare.19303928.v1                  figshare   
354592                   10.5524/102485      GigaScience Database   
20065           10.5061/dryad.7sqv9s4x3                     Dryad   

                                                 subjects  \
30687   [{'subject': 'High Energy Astrophysics Data/X-...   
1675    [{'subject': 'High Energy Astrophysics Data/X-...   
346487  [{'subject': 'Animal physiology - biophysics',...   
354592  [{'lang': 'en-US', 'subject': 'Metagenomic'}, ...   
20065   [{'subject': 'FOS: Biological sciences', 'subj...   

                                       relatedIdentifiers  \
30687                                                 NaN   
1675                                                  NaN   
346487  [{'relationType': 'IsIdenticalTo', 'relatedIde...   
354592                                                NaN   
20065                                                 NaN   

                        sizes   formats rightsIdentifier  \
30687   ks 24.788038547483001  ['FITS']              NaN   
1675    ks 6.1128734903220998  ['FITS']              NaN   
346487            21158 Bytes       NaN        cc-by-4.0   
354592                   1 GB       NaN          cc0-1.0   
20065             92538 bytes       NaN          cc0-1.0   

                                                 creators  num_funders  \
30687   [{'name': 'CXC-DS', 'nameType': 'Organizationa...            1   
1675    [{'name': 'CXC-DS', 'nameType': 'Organizationa...            1   
346487  [{'name': 'Caenorhabditis Intervention Testing...            4   
354592  [{'name': 'Danielle, Wrenn C', 'nameType': 'Pe...            4   
20065   [{'name': 'Swicegood, Amber', 'nameType': 'Per...            4   

                                               awardTitle  awardNumber  \
30687                                Chandra X-ray Center  NAS-8-03060   
1675                                 Chandra X-ray Center  NAS-8-03060   
346487  Caenorhabditis Testing Program Data Coordinati...  U24AG056052   
354592                                                NaN  TL4GM118992   
20065                                                 NaN   F16AC01242   

                                    funder_name  \
30687                                      NASA   
1675                                       NASA   
346487              National Institute on Aging   
354592            National Institutes of Health   
20065   United States Fish and Wildlife Service   

                             funderidentifier funderidentifiertype     ROR_ID  \
30687                        0000000449071619                 ISNI  027ka1x80   
1675    http://isni.org/isni/0000000449071619                 ISNI  027ka1x80   
346487              https://ror.org/049v75w11                  ROR  049v75w11   
354592     https://doi.org/10.13039/100000002   Crossref Funder ID  01cwqze88   
20065               https://ror.org/04k7dar27                  ROR  04k7dar27   

        USFF USFF_2 ROR_cleaned  
30687   True   True   027ka1x80  
1675    True   True   027ka1x80  
346487  True   True   049v75w11  
354592  True   True   01cwqze88  
20065   True   True   04k7dar27

In [167]:
USFF_df.to_csv('2023_USFF.csv', index=False)

# Load data


In [2]:
df = pd.read_csv('2023/2023.csv')
df.head(3)

C:\Users\eschares\AppData\Local\Temp\ipykernel_21856\3780737585.py:1: DtypeWarning: Columns (5,6,12,17,18) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('2023/2023.csv')


top_id  publicationyear  \
0  10.18465/mnt_la_faute_sur_mer_2013             2023   
1  10.18465/mnt_la_faute_sur_mer_2013             2023   
2      10.18465/mnt_jard_sur_mer_2013             2023   

                                  doi  \
0  10.18465/mnt_la_faute_sur_mer_2013   
1  10.18465/mnt_la_faute_sur_mer_2013   
2      10.18465/mnt_jard_sur_mer_2013   

                                           publisher  \
0  Observatoire des Sciences de l'Univers Nantes ...   
1  Observatoire des Sciences de l'Univers Nantes ...   
2  Observatoire des Sciences de l'Univers Nantes ...   

                                            subjects relatedIdentifiers sizes  \
0  [{'subject': 'Géomorphologie', 'valueUri': ''}...                NaN   NaN   
1  [{'subject': 'Géomorphologie', 'valueUri': ''}...                NaN   NaN   
2  [{'subject': 'Géomorphologie', 'valueUri': ''}...                NaN   NaN   

  formats rightsIdentifier                                           creators  \
0     NaN              NaN  [{'name': 'Launeau, Patrick', 'nameType': 'Per...   
1     NaN              NaN  [{'name': 'Launeau, Patrick', 'nameType': 'Per...   
2     NaN              NaN  [{'name': 'Launeau, Patrick', 'nameType': 'Per...   

   num_funders awardTitle awardNumber  \
0            2        NaN         NaN   
1            2        NaN         NaN   
2            2        NaN         NaN   

                                         funder_name  \
0  Direction Régionale de l'Environnement, de l'A...   
1              Conseil Régional des Pays de la Loire   
2  Direction Régionale de l'Environnement, de l'A...   

                        funderidentifier funderidentifiertype     ROR_ID  \
0                                    NaN                  NaN       None   
1  https://doi.org/10.13039/501100013414   Crossref Funder ID  01zsm1k25   
2                                    NaN                  NaN       None   

    USFF USFF_2  
0   None   None  
1  False  False  
2   None   None

In [3]:
df.shape

(365314, 19)

In [16]:
# one False (19660) is a bool, the other False (146356) is a string
# same with True (8), and string (15429)
df['USFF_2'].value_counts()

False    196600
False    146356
True      15429
None       5260
True          8
Name: USFF_2, dtype: int64

In [10]:
df['USFF_2'].value_counts().reset_index().rename(columns={"index": "value", 0: "count"}).to_csv('multiple_Falses.csv')

In [12]:
df['USFF_2'].astype('bool').value_counts()

False    196600
True     168714
Name: USFF_2, dtype: int64

In [18]:
df[df['USFF_2']==True].shape

(8, 19)

In [19]:
df[ df['USFF_2'] == 'False' ].shape

(146356, 19)

In [20]:
df[ df['USFF_2'] == 'False' ]['USFF_2'] = False

C:\Users\eschares\AppData\Local\Temp\ipykernel_21856\2906859847.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[ df['USFF_2'] == 'False' ]['USFF_2'] = False


In [21]:
# didn't work
df['USFF_2'].value_counts()

False    196600
False    146356
True      15429
None       5260
True          8
Name: USFF_2, dtype: int64

In [23]:
df.loc[ df['USFF_2']=='False', ['USFF_2'] ] = False

In [25]:
# did work!
df['USFF_2'].value_counts()

False    342956
True      15429
None       5260
True          8
Name: USFF_2, dtype: int64

In [26]:
df.loc[ df['USFF_2']=='True', ['USFF_2'] ] = True

In [27]:
# did work!
df['USFF_2'].value_counts()

False    342956
True      15437
None       5260
Name: USFF_2, dtype: int64

In [28]:
df.to_csv('2023/2023.csv', index=False)

In [30]:
df[ df['USFF_2']==False ].shape

(342956, 19)

In [171]:
# select USFF true, collapse by DOI, get a final count
notUSFF_df = df[ df['USFF_2']==False ]
notUSFF_df.sample(5)

top_id  publicationyear                      doi  \
11890   10.5061/dryad.gb5mkkwtq             2023  10.5061/dryad.gb5mkkwtq   
147738   10.60712/si-id155405.1             2023   10.60712/si-id155405.1   
198380   10.60712/si-id216033.1             2023   10.60712/si-id216033.1   
106158    10.60712/si-id79773.1             2023    10.60712/si-id79773.1   
36908     10.17632/9rkz5whz39.1             2023    10.17632/9rkz5whz39.1   

                                                publisher  \
11890                                               Dryad   
147738  Leibniz Institute DSMZ - German Collection of ...   
198380  Leibniz Institute DSMZ - German Collection of ...   
106158  Leibniz Institute DSMZ - German Collection of ...   
36908                                            Mendeley   

                                                 subjects  \
11890   [{'subject': 'FOS: Agricultural sciences', 'su...   
147738  [{'subject': 'EUKARYOTA'}, {'subject': 'Collet...   
198380  [{'subject': 'BACTERIA'}, {'subject': 'Cystoba...   
106158  [{'subject': 'EUKARYOTA'}, {'subject': 'Vuille...   
36908                                                 NaN   

                                       relatedIdentifiers          sizes  \
11890   [{'relationType': 'IsCitedBy', 'relatedIdentif...  1224014 bytes   
147738                                                NaN            NaN   
198380                                                NaN            NaN   
106158                                                NaN            NaN   
36908   [{'relationType': 'IsVersionOf', 'relatedIdent...            NaN   

                             formats rightsIdentifier  \
11890                            NaN          cc0-1.0   
147738  ['JSON', 'application/json']        cc-by-4.0   
198380  ['JSON', 'application/json']        cc-by-4.0   
106158  ['JSON', 'application/json']        cc-by-4.0   
36908                            NaN        cc-by-4.0   

                                                 creators  num_funders  \
11890   [{'name': 'Magenau, Elena', 'nameType': 'Perso...            1   
147738  [{'name': 'Reimer, Lorenz C.', 'nameType': 'Pe...            1   
198380  [{'name': 'Reimer, Lorenz C.', 'nameType': 'Pe...            1   
106158  [{'name': 'Reimer, Lorenz C.', 'nameType': 'Pe...            1   
36908   [{'name': 'Jose M. Requena', 'affiliation': []...            1   

                                               awardTitle awardNumber  \
11890                                                 NaN      745012   
147738  NFDI4Microbiota - Nationale Forschungsdateninf...   460129525   
198380  NFDI4Microbiota - Nationale Forschungsdateninf...   460129525   
106158  NFDI4Microbiota - Nationale Forschungsdateninf...   460129525   
36908                                                 NaN         NaN   

                                 funder_name  \
11890                    European Commission   
147738  Deutsche Forschungsgemeinschaft e.V.   
198380  Deutsche Forschungsgemeinschaft e.V.   
106158  Deutsche Forschungsgemeinschaft e.V.   
36908       Agencia Estatal de Investigación   

                               funderidentifier funderidentifiertype  \
11890                 https://ror.org/00k4n6c32                  ROR   
147738                                018mejw64                  ROR   
198380                                018mejw64                  ROR   
106158                                018mejw64                  ROR   
36908   http://dx.doi.org/10.13039/501100011033   Crossref Funder ID   

           ROR_ID   USFF USFF_2  
11890   00k4n6c32  False  False  
147738  018mejw64  False  False  
198380  018mejw64  False  False  
106158  018mejw64  False  False  
36908   003x0zc53  False  False

In [172]:
notUSFF_df.shape

(342956, 19)

In [174]:
# Standardize the ROR column, some are just the ID, some are a link.
# If you want to count them, you need to have them in the same format
notUSFF_df['ROR_cleaned'] = [x.split('/')[-1] for x in notUSFF_df['ROR_ID']]

C:\Users\eschares\AppData\Local\Temp\ipykernel_13240\3500297106.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  notUSFF_df['ROR_cleaned'] = [x.split('/')[-1] for x in notUSFF_df['ROR_ID']]


In [176]:
notUSFF_df.head(3)

top_id  publicationyear  \
1  10.18465/mnt_la_faute_sur_mer_2013             2023   
3      10.18465/mnt_jard_sur_mer_2013             2023   
5       10.18465/mnt_noirmoutier_2013             2023   

                                  doi  \
1  10.18465/mnt_la_faute_sur_mer_2013   
3      10.18465/mnt_jard_sur_mer_2013   
5       10.18465/mnt_noirmoutier_2013   

                                           publisher  \
1  Observatoire des Sciences de l'Univers Nantes ...   
3  Observatoire des Sciences de l'Univers Nantes ...   
5  Observatoire des Sciences de l'Univers Nantes ...   

                                            subjects relatedIdentifiers sizes  \
1  [{'subject': 'Géomorphologie', 'valueUri': ''}...                NaN   NaN   
3  [{'subject': 'Géomorphologie', 'valueUri': ''}...                NaN   NaN   
5  [{'subject': 'Géomorphologie', 'valueUri': ''}...                NaN   NaN   

  formats rightsIdentifier                                           creators  \
1     NaN              NaN  [{'name': 'Launeau, Patrick', 'nameType': 'Per...   
3     NaN              NaN  [{'name': 'Launeau, Patrick', 'nameType': 'Per...   
5     NaN              NaN  [{'name': 'Launeau, Patrick', 'nameType': 'Per...   

   num_funders awardTitle awardNumber                            funder_name  \
1            2        NaN         NaN  Conseil Régional des Pays de la Loire   
3            2        NaN         NaN  Conseil Régional des Pays de la Loire   
5            2        NaN         NaN  Conseil Régional des Pays de la Loire   

                        funderidentifier funderidentifiertype     ROR_ID  \
1  https://doi.org/10.13039/501100013414   Crossref Funder ID  01zsm1k25   
3  https://doi.org/10.13039/501100013414   Crossref Funder ID  01zsm1k25   
5  https://doi.org/10.13039/501100013414   Crossref Funder ID  01zsm1k25   

    USFF USFF_2 ROR_cleaned  
1  False  False   01zsm1k25  
3  False  False   01zsm1k25  
5  False  False   01zsm1k25

In [177]:
notUSFF_df['ROR_cleaned'].value_counts()

018mejw64    293220
00k4n6c32      8423
032e6b942      4343
003x0zc53      3588
01h0zpd94      1916
              ...  
01dqb0q37         1
00q6d2f90         1
03yeq9x20         1
056yktd04         1
02pry0c91         1
Name: ROR_cleaned, Length: 2705, dtype: int64

In [179]:
# save value_counts as a df
notcounts = notUSFF_df['ROR_cleaned'].value_counts().reset_index().rename(columns={"index": "NOTROR_cleaned", 'ROR_cleaned': "count"})
notcounts

NOTROR_cleaned   count
0         018mejw64  293220
1         00k4n6c32    8423
2         032e6b942    4343
3         003x0zc53    3588
4         01h0zpd94    1916
...             ...     ...
2700      01dqb0q37       1
2701      00q6d2f90       1
2702      03yeq9x20       1
2703      056yktd04       1
2704      02pry0c91       1

[2705 rows x 2 columns]

In [180]:
notcounts.to_csv('2023_agency_NOTcounts.csv', index=False)

### Count up the FF agencies

In [168]:
USFF_df['ROR_cleaned'].value_counts()

021nxhr62    4616
027ka1x80    2194
04rc0xn13    1675
01cwqze88    1423
05wqqhv83     468
             ... 
01ds51411       1
05xqpda80       1
05hhm9a98       1
03dm1p143       1
05v3mvq14       1
Name: ROR_cleaned, Length: 188, dtype: int64

In [169]:
# save value_counts as a df
counts = USFF_df['ROR_cleaned'].value_counts().reset_index().rename(columns={"index": "ROR_cleaned", 'ROR_cleaned': "count"})
counts

ROR_cleaned  count
0     021nxhr62   4616
1     027ka1x80   2194
2     04rc0xn13   1675
3     01cwqze88   1423
4     05wqqhv83    468
..          ...    ...
183   01ds51411      1
184   05xqpda80      1
185   05hhm9a98      1
186   03dm1p143      1
187   05v3mvq14      1

[188 rows x 2 columns]

In [170]:
# add year
counts['year'] = 2023
counts

ROR_cleaned  count  year
0     021nxhr62   4616  2023
1     027ka1x80   2194  2023
2     04rc0xn13   1675  2023
3     01cwqze88   1423  2023
4     05wqqhv83    468  2023
..          ...    ...   ...
183   01ds51411      1  2023
184   05xqpda80      1  2023
185   05hhm9a98      1  2023
186   03dm1p143      1  2023
187   05v3mvq14      1  2023

[188 rows x 3 columns]

In [73]:
USFF_visited = json.load(open('Is_ROR_a_USFF_visited_dict.txt',))

In [74]:
len(USFF_visited)

6731

In [75]:
# add True/False, can be False bc sometimes ROR doesn't have it properly ID'd (025g6sc95, President's Emergency Plan for AIDS Relief)
counts['USFF'] = counts['ROR_cleaned'].apply(has_US_govt_parent, visited=USFF_visited)

Checking 021nxhr62
Already found 021nxhr62
Checking 027ka1x80
Already found 027ka1x80
Checking 04rc0xn13
Already found 04rc0xn13
Checking 01cwqze88
Already found 01cwqze88
Checking 05wqqhv83
Already found 05wqqhv83
Checking 040gcmg81
Already found 040gcmg81
Checking 04q48ey07
Already found 04q48ey07
Checking 02916qm60
Already found 02916qm60
Checking 04xeg9z08
Already found 04xeg9z08
Checking 001xhss06
Already found 001xhss06
Checking 04byxyr05
Already found 04byxyr05
Checking 01bj3aw27
Already found 01bj3aw27
Checking 05qx3fv49
Already found 05qx3fv49
Checking 043z4tv69
Already found 043z4tv69
Checking 01s5ya894
Already found 01s5ya894
Checking 00adh9b73
Already found 00adh9b73
Checking 01na82s61
Already found 01na82s61
Checking 05nwjp114
Already found 05nwjp114
Checking 012pb6c26
Already found 012pb6c26
Checking 049v75w11
Already found 049v75w11
Checking 02z5nhe81
Already found 02z5nhe81
Checking 05p847d66
Already found 05p847d66
Checking 00b6sbb32
Already found 00b6sbb32
Checking 00

In [76]:
counts

ROR_cleaned  count  year  USFF
0     021nxhr62   4616  2023  True
1     027ka1x80   2194  2023  True
2     04rc0xn13   1675  2023  True
3     01cwqze88   1423  2023  True
4     05wqqhv83    468  2023  True
..          ...    ...   ...   ...
184   01ds51411      1  2023  True
185   05xqpda80      1  2023  True
186   04jaeeg73      1  2023  True
187   03dm1p143      1  2023  True
188   05v3mvq14      1  2023  True

[189 rows x 4 columns]

In [77]:
def ROR_ID_to_orgname(org_id: str, visited: dict[str, bool] = None) -> str:
    """
    Takes in ROR ID
    Returns organization name
    """
    print(f'Checking {org_id}')
    
    # start with an empty cache
    if visited is None:
        visited = {}

    # if you passed me None, just give it back
    if org_id == 'None':
        return 'None'
    
    # check it here, if we've done it already we're done
    if org_id in visited:
        print(f'Already found {org_id}')
        return visited[org_id]

    # - load the data for an organisation
    #print(f'Loading data for {org_id}')
    
    url = f'https://api.ror.org/organizations/{org_id}'
    api_response = requests.get(url)
    parsed_response = api_response.json()

    result = parsed_response['name']

    # remember we already visited this org id, record its status
    print(f"RESULT {result}")
    visited[org_id] = result

    # - if we didn't return True already, none were the US govt. or had it as a (grand)parent, return False
    return result

In [37]:
ROR_ID_to_orgname('04rc0xn13')

Checking 04rc0xn13
RESULT Environmental Molecular Sciences Laboratory


'Environmental Molecular Sciences Laboratory'

In [79]:
#USFF_agencyname_visited = {}
USFF_agencyname_visited = json.load(open('ROR_to_USFF_agencyname_visited.txt',))

In [80]:
len(USFF_agencyname_visited)

235

In [81]:
%%time
counts['Agency'] = counts['ROR_cleaned'].apply(ROR_ID_to_orgname, visited=USFF_agencyname_visited)

Checking 021nxhr62
Already found 021nxhr62
Checking 027ka1x80
Already found 027ka1x80
Checking 04rc0xn13
Already found 04rc0xn13
Checking 01cwqze88
Already found 01cwqze88
Checking 05wqqhv83
Already found 05wqqhv83
Checking 040gcmg81
Already found 040gcmg81
Checking 04q48ey07
Already found 04q48ey07
Checking 02916qm60
Already found 02916qm60
Checking 04xeg9z08
Already found 04xeg9z08
Checking 001xhss06
Already found 001xhss06
Checking 04byxyr05
Already found 04byxyr05
Checking 01bj3aw27
Already found 01bj3aw27
Checking 05qx3fv49
Already found 05qx3fv49
Checking 043z4tv69
Already found 043z4tv69
Checking 01s5ya894
Already found 01s5ya894
Checking 00adh9b73
Already found 00adh9b73
Checking 01na82s61
Already found 01na82s61
Checking 05nwjp114
Already found 05nwjp114
Checking 012pb6c26
Already found 012pb6c26
Checking 049v75w11
Already found 049v75w11
Checking 02z5nhe81
Already found 02z5nhe81
Checking 05p847d66
Already found 05p847d66
Checking 00b6sbb32
Already found 00b6sbb32
Checking 00

RESULT Connecticut Sea Grant
Checking 033yfkj90
RESULT Naval Postgraduate School
Checking 008qp6e21
RESULT Rehabilitation Research and Development Service
Checking 025g6sc95
Already found 025g6sc95
Checking 01ds51411
Already found 01ds51411
Checking 05xqpda80
Already found 05xqpda80
Checking 04jaeeg73
Already found 04jaeeg73
Checking 03dm1p143
RESULT Naval Sea Systems Command
Checking 05v3mvq14
Already found 05v3mvq14
CPU times: total: 469 ms
Wall time: 16.2 s


In [82]:
len(USFF_agencyname_visited)

267

In [83]:
# save dictionary to file
json.dump(USFF_agencyname_visited, open('ROR_to_USFF_agencyname_visited.txt', 'w'))

In [84]:
counts

ROR_cleaned  count  year  USFF  \
0     021nxhr62   4616  2023  True   
1     027ka1x80   2194  2023  True   
2     04rc0xn13   1675  2023  True   
3     01cwqze88   1423  2023  True   
4     05wqqhv83    468  2023  True   
..          ...    ...   ...   ...   
184   01ds51411      1  2023  True   
185   05xqpda80      1  2023  True   
186   04jaeeg73      1  2023  True   
187   03dm1p143      1  2023  True   
188   05v3mvq14      1  2023  True   

                                                Agency  
0                          National Science Foundation  
1        National Aeronautics and Space Administration  
2          Environmental Molecular Sciences Laboratory  
3                        National Institutes of Health  
4                           Division of Ocean Sciences  
..                                                 ...  
184                    Texas Sea Grant College Program  
185           Office of Ocean Exploration and Research  
186                     Wyoming Space Grant Consortium  
187                          Naval Sea Systems Command  
188  National Energy Research Scientific Computing ...  

[189 rows x 5 columns]

In [85]:
counts.to_csv('2023_agency_counts.csv', index=False)

### Collapse by DOI

In [181]:
# call groupby and pass the name of the column you want to group on
# then use [''] to specify columns to perform actual aggregation on
# as_index=False keeps doi from becoming index

test = USFF_df.groupby(['doi', 'publicationyear', 'publisher', 'num_funders'], as_index=False)['ROR_cleaned'].count()
test.head(5)

doi  publicationyear  \
0     10.1184/r1/22010888             2023   
1  10.1184/r1/22010888.v1             2023   
2     10.1184/r1/24481162             2023   
3  10.1184/r1/24481162.v1             2023   
4            10.12686/a21             2023   

                             publisher  num_funders  ROR_cleaned  
0           Carnegie Mellon University            2            2  
1           Carnegie Mellon University            2            2  
2           Carnegie Mellon University            1            1  
3           Carnegie Mellon University            1            1  
4  ETHZ, IPGP, JPL, ICL, Univ. Bristol            5            1

In [182]:
test.shape

(10569, 5)

In [88]:
test.sample(10)

doi  publicationyear  \
6658                10.3886/icpsr38924             2023   
6613             10.3886/icpsr38850.v1             2023   
9408            10.5281/zenodo.8169839             2023   
340             10.17603/ds2-nwzy-tf07             2023   
102                    10.15784/601680             2023   
185             10.1594/pangaea.954602             2023   
10191  10.6084/m9.figshare.23834814.v1             2023   
7375           10.5061/dryad.69p8cz97c             2023   
2080                    10.25574/25305             2023   
2520                    10.25574/26836             2023   

                                               publisher  num_funders  \
6658   ICPSR - Interuniversity Consortium for Politic...            1   
6613   ICPSR - Interuniversity Consortium for Politic...            3   
9408                                              Zenodo            1   
340                                        Designsafe-CI            2   
102            U.S. Antarctic Program (USAP) Data Center            1   
185                                              PANGAEA            2   
10191                                           figshare           10   
7375                                               Dryad            3   
2080                            Chandra X-ray Center/SAO            1   
2520                            Chandra X-ray Center/SAO            1   

       ROR_cleaned  
6658             1  
6613             2  
9408             1  
340              1  
102              1  
185              2  
10191            8  
7375             1  
2080             1  
2520             1

In [89]:
test[ test['num_funders']!=test['ROR_cleaned']]

doi  publicationyear  \
4                10.12686/a21             2023   
5      10.12751/g-node.1b9v1w             2023   
7      10.12751/g-node.8s1yed             2023   
11     10.12751/g-node.wf9cbv             2023   
12     10.12751/g-node.xrxt9n             2023   
...                       ...              ...   
10559       10.7924/r4x35002b             2023   
10560       10.7924/r4zw1n02x             2023   
10563     10.7936/6rxs-103632             2023   
10564     10.7936/6rxs-103641             2023   
10566     10.7936/6rxs-103645             2023   

                                 publisher  num_funders  ROR_cleaned  
4      ETHZ, IPGP, JPL, ICL, Univ. Bristol            5            1  
5                                   G-Node           13           10  
7                                   G-Node            4            2  
11                                  G-Node            3            1  
12                                  G-Node            4            3  
...                                    ...          ...          ...  
10559        Duke Research Data Repository            2            1  
10560        Duke Research Data Repository            2            1  
10563   Washington University in St. Louis            3            2  
10564                              Unknown            3            1  
10566   Washington University in St. Louis            3            2  

[1578 rows x 5 columns]

In [183]:
test.to_csv('2023_USFF_byDOI.csv', index=False)